In [1]:
import sys
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [12]:
ih_df = pd.read_csv("GSE158666-GPL21103-ih.txt", sep="\t", header=0) 
gsm_dict = {'mdx_IL5Tg_S1':'GSM4805200', 'mdx_S4':'GSM4805197', 'IL5Tg_S7':'GSM4805194', 'mdx_IL5Tg_S2':'GSM4805201',\
            'mdx_S5':'GSM4805198', 'IL5Tg_S8':'GSM4805195', 'mdx_IL5Tg_S3':'GSM4805202', 'mdx_S6':'GSM4805199',\
            'IL5Tg_S9':'GSM4805196'}
ih_df

ArrayID ArrayHeader                      ClinicalHeader
0  GSM4805194  GSM4805194      replicate 1 of IL5Tg condition
1  GSM4805195  GSM4805195      replicate 2 of IL5Tg condition
2  GSM4805196  GSM4805196      replicate 3 of IL5Tg condition
3  GSM4805197  GSM4805197        replicate 1 of mdx condition
4  GSM4805198  GSM4805198        replicate 2 of mdx condition
5  GSM4805199  GSM4805199        replicate 3 of mdx condition
6  GSM4805200  GSM4805200  replicate 1 of mdx_IL5Tg condition
7  GSM4805201  GSM4805201  replicate 2 of mdx_IL5Tg condition
8  GSM4805202  GSM4805202  replicate 3 of mdx_IL5Tg condition

In [13]:
expr = pd.DataFrame(pd.read_csv("GSE158666_RawCountFile_RSEM_genes.txt", sep="\t", header=0))
expr.columns = ["Name", "ProbeID"]+[gsm_dict[i] for i in expr.columns[2:]]
cols = ["ProbeID", "Name"]+list(expr.columns[2:])
expr = expr[cols]
expr

ProbeID                   Name  GSM4805200  GSM4805197  \
0              Gnai3   ENSMUSG00000000001.4     30198.0    15913.52   
1               Pbsn  ENSMUSG00000000003.15         0.0        0.00   
2              Cdc45  ENSMUSG00000000028.15       143.0      159.00   
3                H19  ENSMUSG00000000031.16       542.0     4673.99   
4              Scml2  ENSMUSG00000000037.16         3.0       33.00   
...              ...                    ...         ...         ...   
54141  RP23-174D11.6   ENSMUSG00000116995.1       173.0      164.00   
54142   RP23-452G1.4   ENSMUSG00000116996.1         0.0        0.00   
54143  RP23-396K21.4   ENSMUSG00000116997.1         0.0        0.00   
54144   RP23-176C2.2   ENSMUSG00000116998.1         0.0        0.00   
54145   RP24-299G8.2   ENSMUSG00000116999.1         0.0        0.00   

       GSM4805194  GSM4805201  GSM4805198  GSM4805195  GSM4805202  GSM4805199  \
0        15039.11     23970.0     12457.0    17457.74     23069.0     13541.0   
1            0.00         0.0         0.0        0.00         0.0         0.0   
2          364.00       122.0        57.0       93.00        94.0       168.0   
3           70.00       990.0      1252.0       53.00       796.0      1186.0   
4            2.00         2.0         1.0        2.00         0.0        10.0   
...           ...         ...         ...         ...         ...         ...   
54141      103.00       153.0        82.0      126.00       143.0       195.0   
54142        0.00         0.0         0.0        0.00         0.0         0.0   
54143        0.00         0.0         0.0        0.00         0.0         0.0   
54144        0.00         0.0         0.0        0.00         0.0         0.0   
54145        0.00         0.0         0.0        0.00         0.0         0.0   

       GSM4805196  
0        15300.59  
1            0.00  
2          140.00  
3           35.00  
4            4.00  
...           ...  
54141       98.00  
54142        0.00  
54143        0.00  
54144        0.00  
54145        0.00  

[54146 rows x 11 columns]

In [15]:
genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

path_dir = "./"
expr.to_csv(path_dir+"GSE158666-GPL21103-expr.txt", header=True, index=False,sep='\t')
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID                   Name  GSM4805200  GSM4805197  \
0              Gnai3   ENSMUSG00000000001.4    7.483726    7.224766   
1               Pbsn  ENSMUSG00000000003.15    0.000000    0.000000   
2              Cdc45  ENSMUSG00000000028.15    5.180405    5.331998   
3                H19  ENSMUSG00000000031.16    6.074009    6.896458   
4              Scml2  ENSMUSG00000000037.16    1.279284    3.961619   
...              ...                    ...         ...         ...   
54141  RP23-174D11.6   ENSMUSG00000116995.1    5.329731    5.353853   
54142   RP23-452G1.4   ENSMUSG00000116996.1    0.000000    0.000000   
54143  RP23-396K21.4   ENSMUSG00000116997.1    0.000000    0.000000   
54144   RP23-176C2.2   ENSMUSG00000116998.1    0.000000    0.000000   
54145   RP24-299G8.2   ENSMUSG00000116999.1    0.000000    0.000000   

       GSM4805194  GSM4805201  GSM4805198  GSM4805195  GSM4805202  GSM4805199  \
0        7.339751    7.465943    7.338706    7.416912    7.492542    7.238292   
1        0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
2        6.090051    5.258279    4.894574    5.257606    5.070803    5.481612   
3        5.027986    6.480063    6.664083    4.797174    6.413631    6.491682   
4        1.442897    1.174032    0.921560    1.424536    0.000000    2.835988   
...           ...         ...         ...         ...         ...         ...   
54141    5.323161    5.428144    5.190113    5.478510    5.402308    5.579670   
54142    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
54143    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
54144    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
54145    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   

       GSM4805196  
0        7.418550  
1        0.000000  
2        5.644051  
3        4.548604  
4        2.242384  
...           ...  
54141    5.400379  
54142    0.000000  
54143    0.000000  
54144    0.000000  
54145    0.000000  

[54146 rows x 11 columns]

In [16]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE158666-GPL21103-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE158666-GPL21103-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
